In [1]:
%matplotlib inline

In [2]:
import scipy as sp
def logloss(act, pred):
    epsilon = 1e-15
    pred = sp.maximum(epsilon, pred)
    pred = sp.minimum(1-epsilon, pred)
    ll = sum(act*sp.log(pred) + sp.subtract(1,act)*sp.log(sp.subtract(1,pred)))
    ll = ll * -1.0/len(act)
    return ll

In [3]:
from scipy import stats as st
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

sns.set_context("poster")

In [31]:
# A whole world of potential analysis...
kobe = pd.read_csv('data/data.csv')
kobe['known_data'] = kobe['shot_made_flag'].apply(lambda x: 0 if pd.isnull(x) else 1)

In [32]:
print len(kobe)

30697


In [ ]:
kobe.head()

In [33]:
kobe_coltypes = pd.DataFrame(kobe.dtypes.reset_index())
kobe_coltypes.columns = ['col','type']
kobe_coltypes

col     type
0          action_type   object
1   combined_shot_type   object
2        game_event_id    int64
3              game_id    int64
4                  lat  float64
5                loc_x    int64
6                loc_y    int64
7                  lon  float64
8    minutes_remaining    int64
9               period    int64
10            playoffs    int64
11              season   object
12   seconds_remaining    int64
13       shot_distance    int64
14      shot_made_flag  float64
15           shot_type   object
16      shot_zone_area   object
17     shot_zone_basic   object
18     shot_zone_range   object
19             team_id    int64
20           team_name   object
21           game_date   object
22             matchup   object
23            opponent   object
24             shot_id    int64
25          known_data    int64

Attempt 1 - Lets just take the average for each known shot up to that shot
--

In [40]:
kobe['rolling_perc'] = pd.rolling_mean(kobe['shot_made_flag'],window=len(kobe['shot_made_flag']),min_periods=1).fillna(0.5)

/Users/apatterson/Envs/kaggles/lib/python2.7/site-packages/ipykernel/__main__.py:1: FutureWarning: pd.rolling_mean is deprecated for Series and will be removed in a future version, replace with 
	Series.rolling(min_periods=1,window=30697,center=False).mean()
  if __name__ == '__main__':


In [58]:
kobe_output = pd.DataFrame(kobe['rolling_perc'][kobe['known_data']==0])
kobe_output['id'] = kobe_output.index
kobe_output['id'] = kobe_output['id']+1
kobe_output.columns = ['shot_made_flag','shot_id']

In [59]:
kobe_output[['shot_id','shot_made_flag']].to_csv('data/first_attempt.csv',index=False)

Submission logloss: 0.68855
    
Better than 50% mark but not by much!

Attempt 2 - Lets take previous attempt for small sample (Anything with less than 200) and then an incremental naive bayes for the rest
----

In [8]:
from sklearn.naive_bayes import BernoulliNB

In [5]:
kobe_id = pd.read_csv('data/kobe_x_id.csv')
kobe_x = pd.read_csv('data/kobe_x.csv')
kobe_y = pd.read_csv('data/kobe_y.csv')

In [ ]:
from sklearn.naive_bayes import BernoulliNB

i=0
score = []
bnb = BernoulliNB()
new_scores = []
for x, y in zip(kobe_x.iterrows(),kobe_y.iterrows()):
    if i==0:
        print x[1], y[1]
#        score.append([i,0.5])
#        i+=1
#    elif pd.notnull(y['shot_made_flag']):
#        bnb.partial_fit(x,y['shot_made_flag'],[0,1])
#    else:
#        score.append([i,bnb.predict_proba(x)[0][1]])
    

lat                                              33.9723
lon                                            -118.1028
minutes_remaining                                10.0000
period                                            1.0000
playoffs                                          0.0000
seconds_remaining                                27.0000
shot_distance                                    18.0000
game_year                                      2000.0000
game_month                                       10.0000
game_week                                        44.0000
game_dayofweek                                    1.0000
action_type_Alley Oop Dunk Shot                   0.0000
action_type_Alley Oop Layup shot                  0.0000
action_type_Cutting Finger Roll Layup Shot        0.0000
action_type_Cutting Layup Shot                    0.0000
action_type_Driving Bank shot                     0.0000
action_type_Driving Dunk Shot                     0.0000
action_type_Driving Finger Roll

In [ ]:
score = []

for i in test_x.index:
    #print i, train_y[i]
    if i == 0:
        sc = 0.5
        score.append([i,0.5])
    elif i > 0 and i < 200:
        temp_x = train_x[train_x.index< i]
        temp_y = train_y['shot_made_flag'][0:len(temp_x)]
        sc = sum(temp_y)/len(temp_y)
        score.append([i,sum(temp_y)/len(temp_y)])
    else:
        temp_x = train_x[train_x.index< i]
        temp_y = train_y['shot_made_flag'][0:len(temp_x)]
        lrm = LogisticRegression()
        lrm.fit(temp_x,temp_y)
        sc = lrm.predict_proba(test_x[test_x.index==i])[0][1]
    print [i,sc]
    score.append([i,sc])

print score

[0, 0.5]
[7, 0.5]
[16, 0.42857142857142855]
[19, 0.4375]
[32, 0.39285714285714285]
[33, 0.39285714285714285]
[34, 0.39285714285714285]
[35, 0.39285714285714285]
[36, 0.39285714285714285]
[37, 0.39285714285714285]
[44, 0.44117647058823528]
[49, 0.47368421052631576]
[54, 0.42857142857142855]
[59, 0.45652173913043476]
[65, 0.45098039215686275]
[66, 0.45098039215686275]
[70, 0.46296296296296297]
[79, 0.45161290322580644]
[84, 0.43939393939393939]
[85, 0.43939393939393939]
[94, 0.47297297297297297]
[103, 0.48780487804878048]
[112, 0.45555555555555555]
[122, 0.45454545454545453]
[125, 0.46534653465346537]
[132, 0.46728971962616822]
[140, 0.45614035087719296]
[143, 0.44827586206896552]
[149, 0.45454545454545453]
[151, 0.45901639344262296]
[152, 0.45901639344262296]
[155, 0.45161290322580644]
[158, 0.44444444444444442]
[164, 0.4580152671755725]
[171, 0.45255474452554745]
[181, 0.43835616438356162]
[191, 0.43870967741935485]
[192, 0.43870967741935485]
[195, 0.43949044585987262]
[201, 0.17272435

In [ ]:
with open('data/attempt_2_submission.csv','w') as f:
    f.write('shot_id,shot_made_flag'+'\n')
    for line in score:
        f.write(','.join([str(line[0]+1),str(line[1])])+'\n')